### Base de Dados

**Input**: 
* input/by_date/factors/YYYYMMDD.csv - fatores de todas ações listadas na NYSE na frequência de um minuto do dia DD-MM-YYYY.
* input/by_date/returns/YYYYMMDD.csv - retornos de todas ações listadas na NYSE na frequência de um minuto do dia DD-MM-YYYY.

**Output**: 
* output/data/by_date/equal_weighted/median_breakpoint/YYYYMMDD.csv - retornos com as três primeiras defasagens de todas ações listadas na NYSE e portfólios baseado em fatores a partir desses ativos na frequência de um minuto do dia DD-MM-YYYY.

O objetivo desse notebook é juntar duas bases de dados, uma contendo dados de retornos das ações e outro contendo os decis de cada ação. A partir desse merge, vamos criar portfólios equal_weighted dos fatores utilizando a mediana como breakpoint

In [1]:
# pacotes
import numpy as np
import pandas as pd

In [2]:
# oculta mensagens de avisos
import warnings
warnings.filterwarnings("ignore")

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
# factors dataframe
factors = pd.read_csv('../../../input/by_date/factors/20050103.csv', index_col=0)

In [5]:
# precisamos dropar todas ações que não tem TAQ_TICKER, pois é a única variável q conseguimos ligar na outra base
factors = factors[factors['TAQ_TICKER'] != '<undefined>']

In [6]:
factors

date                         COMNAM TAQ_TICKER    MARKETCAP  \
10001  20050103                ENERGY WEST INC       EWST     17335.33   
10002  20050103  BANCTRUST FINANCIAL GROUP INC       BTFG    262630.43   
10012  20050103      D P A C TECHNOLOGIES CORP       DPAC     20646.84   
10025  20050103           A E P INDUSTRIES INC       AEPI    124562.10   
10026  20050103         J & J SNACK FOODS CORP       JJSF    428905.88   
...         ...                            ...        ...          ...   
92655  20050103         UNITEDHEALTH GROUP INC        UNH  56617343.98   
92663  20050103      BANKUNITED FINANCIAL CORP      BKUNA    938952.00   
92807  20050103        AMERISERV FINANCIAL INC       ASRV    102139.24   
92874  20050103             VIDEO DISPLAY CORP       VIDE    118120.40   
93105  20050103               W HOLDING CO INC        WHI   2504277.02   

       pNYSE_size  pNYSE_value  pNYSE_prof  pNYSE_dur  pNYSE_valprof  \
10001        10.0         10.0         1.0        NaN            6.0   
10002        10.0          NaN         NaN        NaN            NaN   
10012        10.0          7.0         8.0        7.0            9.0   
10025        10.0          7.0         7.0        8.0            9.0   
10026         9.0          6.0         9.0        7.0           10.0   
...           ...          ...         ...        ...            ...   
92655         1.0          NaN         NaN        NaN            NaN   
92663         7.0          NaN         NaN        NaN            NaN   
92807        10.0          NaN         NaN        NaN            NaN   
92874        10.0          4.0         8.0        5.0            8.0   
93105         5.0          NaN         NaN        NaN            NaN   

       pNYSE_fscore  pNYSE_debtiss  pNYSE_repurch  pNYSE_nissa  \
10001             1           10.0            1.0          8.0   
10002             1           10.0            1.0          1.0   
10012            10           10.0           10.0          1.0   
10025             1           10.0            1.0          3.0   
10026            10           10.0           10.0          5.0   
...             ...            ...            ...          ...   
92655            10            1.0           10.0          3.0   
92663             1           10.0            1.0          5.0   
92807             1           10.0            1.0          7.0   
92874             1            1.0           10.0          2.0   
93105             1           10.0            1.0          4.0   

       pNYSE_accruals  pNYSE_growth  pNYSE_aturnover  pNYSE_gmargins  \
10001            10.0           5.0              8.0             1.0   
10002             NaN           NaN              NaN             NaN   
10012             5.0           2.0              8.0             5.0   
10025             3.0           9.0              9.0             3.0   
10026             2.0           5.0              9.0             7.0   
...               ...           ...              ...             ...   
92655             NaN           NaN              NaN             NaN   
92663             NaN           NaN              NaN             NaN   
92807             NaN           NaN              NaN             NaN   
92874             8.0           9.0              8.0             6.0   
93105             NaN           NaN              NaN             NaN   

       pNYSE_divp  pNYSE_ep  pNYSE_cfp  pNYSE_noa  pNYSE_inv  pNYSE_invcap  \
10001        10.0       2.0        9.0        7.0        8.0           7.0   
10002         8.0       5.0        3.0        NaN        NaN           NaN   
10012         NaN       8.0        7.0        4.0        6.0           4.0   
10025         NaN       1.0        6.0        NaN        5.0           8.0   
10026         NaN       7.0        8.0        6.0        5.0           3.0   
...           ...       ...        ...        ...        ...           ...   
92655         1.0       6.0        3.0        NaN    

In [7]:
# returns dataframe
returns = pd.read_csv('../../../input/by_date/returns/20050103.csv', index_col=0)

In [8]:
returns.head()

A        AA  AAC      AACE       AAI      AAII  AAME      AANB  \
Time                                                                           
93100  0.000000  0.000000  0.0  0.000000  0.000000 -0.003008   0.0  0.000050   
93200 -0.000830  0.000000  0.0  0.000000  0.000000  0.000000   0.0 -0.064589   
93300  0.000415 -0.002519  0.0  0.000000  0.002769  0.000000   0.0  0.000000   
93400  0.000415 -0.003790  0.0 -0.000340  0.009174 -0.009077   0.0  0.025278   
93500 -0.000415  0.000000  0.0  0.005089  0.003646  0.012085   0.0  0.000000   

       AAON  AAP      AAPL      AATK      ABAX       ABC      ABCB      ABCO  \
Time                                                                           
93100   0.0  0.0  0.003083 -0.038608 -0.008043  0.000000 -0.018745  0.000000   
93200   0.0  0.0  0.000000  0.000000  0.000000 -0.000852  0.000000 -0.004254   
93300   0.0  0.0 -0.002311  0.000000  0.000000 -0.003931  0.000000  0.000000   
93400   0.0  0.0 -0.000309  0.003973 -0.004722 -0.001199  0.000000  0.000000   
93500   0.0  0.0 -0.003246 -0.004415 -0.001353  0.000343  0.000000 -0.003737   

           ABCW  ABFI      ABFS  ABG      ABGX       ABI      ABIX  ABK  ABL  \
Time                                                                           
93100 -0.000342   0.0 -0.000439  0.0 -0.004824  0.000000  0.024693  0.0  0.0   
93200  0.000342   0.0 -0.004162  0.0  0.000000  0.000000  0.000000  0.0  0.0   
93300 -0.011527   0.0  0.005041  0.0  0.003861 -0.000952  0.000000  0.0  0.0   
93400  0.000000   0.0  0.002851  0.0  0.000000  0.000952  0.000000  0.0  0.0   
93500  0.000000   0.0 -0.001073  0.0  0.000963  0.001902  0.000000  0.0  0.0   

       ABLE       ABM  ABMC      ABMD  ABP  ABRI      ABRX       ABS  \
Time                                                                   
93100   0.0  0.000000   0.0  0.005342  0.0   0.0  0.000354  0.000000   
93200   0.0  0.000000   0.0 -0.003453  0.0   0.0  0.000000  0.000000   
93300   0.0 -0.002034   0.0 -0.005613  0.0   0.0  0.000000  0.000000   
93400   0.0  0.000000   0.0  0.002464  0.0   0.0  0.004504  0.000000   
93500   0.0  0.002541   0.0 -0.001895  0.0   0.0  0.002640  0.000416   

            ABT  ABVA      ACAP      ACAS  ACAT  ACBA      ACDO  ACEC  \
Time                                                                    
93100  0.000000   0.0  0.000000  0.000000   0.0   0.0  0.000000   0.0   
93200 -0.000215   0.0  0.005345  0.000897   0.0   0.0  0.000000   0.0   
93300 -0.002153   0.0  0.001088  0.000000   0.0   0.0  0.001077   0.0   
93400  0.000711   0.0  0.000000  0.000896   0.0   0.0  0.002865   0.0   
93500  0.002302   0.0  0.000000  0.002087   0.0   0.0  0.001072   0.0   

           ACET       ACF  ACI      ACLS      ACME      ACMR  ACO  ACPW  \
Time                                                                      
93100  0.004761  0.000000  0.0 -0.008626 -0.004240  0.005565  0.0   0.0   
93200  0.008931 -0.002125  0.0 -0.001238  0.000000  0.000000  0.0   0.0   
93300  0.000000  0.016878  0.0  0.000000  0.001415  0.000000  0.0   0.0   
93400  0.002612 -0.000837  0.0  0.001238  0.000000  0.000000  0.0   0.0   
93500  0.000000  0.000419  0.0 -0.001238  0.000000  0.000000  0.0   0.0   

            ACR       ACS      ACTG      ACTL      ACTT      ACTU  ACU  \
Time                                                                     
93100  0.000000  0.000000  0.000000  0.000000  0.052056  0.000000  0.0   
93200  0.000000 -0.000825 -0.032601  0.002845  0.000000  0.000000  0.0   
93300  0.000000 -0.000661  0.000000  0.000000  0.000000  0.019418  0.0   
93400  0.000000  0.000661  0.000000  0.000000 -0.000725  0.003839  0.0   
93500  0.003387 -0.002149  0.000000  0.001703  0.000000 -0.015444  0.0   

            ACV      ACXM        AD      ADAM      ADAT      ADBE      ADBL  \
Time                                                                          
93100  0.000000  0.004535  0.000000  0.000000  0.004866  0.000000  0.010811   
93200 -0.000824 -0.000189  0.000

### Functions

Como a metodologia para se criar o portfólio é a mesma, isso é, comprado em todos ativos acima da mediana e vendido em todos ativos abaixo da mediana, vamos criar funções que façam isso recebendo a coluna do fator em questão como parâmetro

In [9]:
def portfolio_position(col):
    long_position = []      # posição comprado
    short_position = []     # posição vendido  

    # primeiro, precisamos dropar as linhas tais que tem valor NaN no parâmetro de localidade do fator
    temp = factors[factors[col].notna()]
    """
    Criamos um loop com o critério:
    acima da mediana '5' (estritamente), então o portfolio assume a posição comprado
    abaixo da mediana '5' (fracamente), então o portfolio assume a posição vendido
    """
    for permno in temp.index:
        if temp.loc[permno][col] > 5:
            long_position.append(temp.loc[permno]['TAQ_TICKER'])
        else:
            short_position.append(temp.loc[permno]['TAQ_TICKER'])
    """
    agora precisamos criar dois loops, um para cada lista:
    o loop deve verificar se o ticker dentro da lista é uma das colunas da base de retornos,
    isso é, verifica se temos dados de retornos para essa ação.
    """

    drop_long_position = []
    drop_short_position = []

    for ticker in long_position:
        if ticker not in returns.columns:
            drop_long_position.append(ticker)

    for ticker in drop_long_position:
        long_position.remove(ticker)

    for ticker in short_position:   
        if ticker not in returns.columns:
            drop_short_position.append(ticker)

    for ticker in drop_short_position:
        short_position.remove(ticker)

    return(long_position, short_position)

In [10]:
def portfolio_formation(col):
    # usaremos a função portfolio_position() para obtermos as firmas na posição comprada e vendida
    long_position, short_position = portfolio_position(col)
    # a nova coluna do fator se chamará:
    new_col = col[6].upper() + col[7:] + ' Factor'
    """
    O portfolio é formado subtraindo os retornos médio (equal weighted) das ações em short_position
    dos retornos médio (equal weighted) das ações em long_position
    """
    returns[new_col] = returns[long_position].mean(axis=1) - returns[short_position].mean(axis=1)

### Loop para criar todos fatores

In [16]:
pNYSE_factors = factors.columns[4:]

In [18]:
# para cada coluna de pNYSE_factors, formamos um portfolio
for pNYSE in pNYSE_factors:
    portfolio_formation(pNYSE)

In [19]:
returns

A        AA       AAC      AACE       AAI      AAII  AAME  \
Time                                                                       
93100   0.000000  0.000000  0.000000  0.000000  0.000000 -0.003008   0.0   
93200  -0.000830  0.000000  0.000000  0.000000  0.000000  0.000000   0.0   
93300   0.000415 -0.002519  0.000000  0.000000  0.002769  0.000000   0.0   
93400   0.000415 -0.003790  0.000000 -0.000340  0.009174 -0.009077   0.0   
93500  -0.000415  0.000000  0.000000  0.005089  0.003646  0.012085   0.0   
...          ...       ...       ...       ...       ...       ...   ...   
155600  0.000419  0.000162  0.000000  0.000000  0.002824  0.002981   0.0   
155700  0.000419  0.000807 -0.024693  0.000000  0.000000  0.005935   0.0   
155800  0.000000  0.000484  0.000000  0.001763  0.000939  0.000000   0.0   
155900  0.000419 -0.000161  0.000000  0.002112 -0.001880  0.002954   0.0   
160000  0.000419  0.000000  0.024693  0.002107  0.002818  0.000000   0.0   

            AANB      AAON       AAP      AAPL      AATK      ABAX       ABC  \
Time                                                                           
93100   0.000050  0.000000  0.000000  0.003083 -0.038608 -0.008043  0.000000   
93200  -0.064589  0.000000  0.000000  0.000000  0.000000  0.000000 -0.000852   
93300   0.000000  0.000000  0.000000 -0.002311  0.000000  0.000000 -0.003931   
93400   0.025278  0.000000  0.000000 -0.000309  0.003973 -0.004722 -0.001199   
93500   0.000000  0.000000  0.000000 -0.003246 -0.004415 -0.001353  0.000343   
...          ...       ...       ...       ...       ...       ...       ...   
155600  0.000000  0.000000 -0.000229 -0.000158  0.000000  0.000000 -0.000688   
155700  0.000000  0.003337  0.000000  0.000237  0.000000  0.000000  0.000172   
155800  0.000000  0.000000  0.000229 -0.000079  0.000000 -0.001421 -0.000172   
155900  0.000000  0.000000 -0.000229  0.000158 -0.004535  0.000711  0.000172   
160000  0.000000  0.000000 -0.002981  0.000000  0.000000 -0.001422  0.000172   

            ABCB      ABCO      ABCW      ABFI      ABFS       ABG      ABGX  \
Time                                                                           
93100  -0.018745  0.000000 -0.000342  0.000000 -0.000439  0.000000 -0.004824   
93200   0.000000 -0.004254  0.000342  0.000000 -0.004162  0.000000  0.000000   
93300   0.000000  0.000000 -0.011527  0.000000  0.005041  0.000000  0.003861   
93400   0.000000  0.000000  0.000000  0.000000  0.002851  0.000000  0.000000   
93500   0.000000 -0.003737  0.000000  0.000000 -0.001073  0.000000  0.000963   
...          ...       ...       ...       ...       ...       ...       ...   
155600  0.000000  0.000268  0.000691  0.000000  0.001338  0.000000  0.002934   
155700  0.000000 -0.002413 -0.001037  0.000000 -0.002231  0.000000  0.000976   
155800  0.000000 -0.000806 -0.000346  0.000000  0.002231  0.000000  0.000000   
155900  0.000488  0.000806  0.000000  0.000000  0.000000  0.002888  0.000000   
160000  0.000000  0.000000 -0.004856  0.017858  0.001113  0.000000 -0.001953   

             ABI      ABIX       ABK  ABL  ABLE       ABM      ABMC      ABMD  \
Time                                                                            
93100   0.000000  0.024693  0.000000  0.0   0.0  0.000000  0.000000  0.005342   
93200   0.000000  0.000000  0.000000  0.0   0.0  0.000000  0.000000 -0.003453   
93300  -0.000952  0.000000  0.000000  0.0   0.0 -0.002034  0.000000 -0.005613   
93400   0.000952  0.000000  0.000000  0.0   0.0  0.000000  0.000000  0.002464   
93500   0.001902  0.000000  0.000000  0.0   0.0  0.002541  0.000000 -0.001895   
...          ...       ...       ...  ...   ...       ...       ...       ...   
155600 -0.001434 -0.005079  0.000485  0.0   0.0  0.000000  0.000000 -0.001995   
155700  0.002389  0.000000 -0.000364  0.0   0.0 -0.002113  0.000000  0.000000   
155800  0.000954  0.000000  0.000121  0.0   0.0 -0.005302  0.000000 -0.001332   
155900  0.000000 -0.001019  0.000000  0.0   0.0  0.00